# Задача про прогнозирование нагрузки на базовые станции сети сотовой связи

Импорт библиотек

In [1]:
import numpy as np
import pandas as pd

Чтение тренировочного и тестового датасетов

In [2]:
train = pd.read_csv('train.csv', parse_dates=['date_'])
test  = pd.read_csv('test.csv', parse_dates=['date_'])

In [3]:
train

ID      date_        spd     subs           trf    y    x  tech  \
0           156 2016-01-01  37.141827  4.11212  18540.512109  600  600     2   
1           156 2016-01-02  32.023205  3.48995  13400.974802  600  600     2   
2           156 2016-01-03  30.754111  2.08728   6407.688203  600  600     2   
3           156 2016-01-04  39.920226  1.86428   7952.696402  600  600     2   
4           156 2016-01-05  32.165091  1.95571   7350.516127  600  600     2   
...         ...        ...        ...      ...           ...  ...  ...   ...   
918854  9998143 2016-10-27   3.909855  5.16468   4203.272346 -800    0     4   
918855  9998143 2016-10-28   4.253848  4.08982   3559.559577 -800    0     4   
918856  9998143 2016-10-29   4.104481  2.73175   2283.362506 -800    0     4   
918857  9998143 2016-10-30   4.619465  3.84675   3276.796623 -800    0     4   
918858  9998143 2016-10-31   6.399519  2.78527   3662.797084 -800    0     4   

          cap  HEIGHT  AZIMUTH  
0       13.00   74.20      160  
1       13.00   74.20      160  
2       13.00   74.20      160  
3       13.00   74.20      160  
4       13.00   74.20      160  
...       ...     ...      ...  
918854   3.25  103.88      -40  
918855   3.25  103.88      -40  
918856   3.25  103.88      -40  
918857   3.25  103.88      -40  
918858   3.25  103.88      -40  

[918859 rows x 11 columns]

In [4]:
test

ID      date_    y    x  tech    cap  HEIGHT  AZIMUTH
0           156 2016-11-02  600  600     2  13.00   74.20      160
1           156 2016-11-03  600  600     2  13.00   74.20      160
2           156 2016-11-04  600  600     2  13.00   74.20      160
3           156 2016-11-05  600  600     2  13.00   74.20      160
4           156 2016-11-06  600  600     2  13.00   74.20      160
...         ...        ...  ...  ...   ...    ...     ...      ...
380866  9998143 2017-02-25 -800    0     4   3.25  103.88      -40
380867  9998143 2017-02-26 -800    0     4   3.25  103.88      -40
380868  9998143 2017-02-27 -800    0     4   3.25  103.88      -40
380869  9998143 2017-02-28 -800    0     4   3.25  103.88      -40
380870  9998143 2017-03-01 -800    0     4   3.25  103.88      -40

[380871 rows x 8 columns]

Целевые переменные

In [5]:
targets = ['spd']

В качестве предсказания используется среднее значение по всем датам для каждой базовой станции

In [6]:
means = train.groupby(by='ID').aggregate('mean')[targets]

Для новых базовых станций предсказывается среднее значение по всем станциям

In [7]:
new_ids = set(test.ID.unique()) - set(train.ID.unique())

mean = means.mean()
for i in new_ids:
    means.loc[i] = mean

In [8]:
means

spd
ID                
156      81.977709
4934      9.321471
10408    76.864349
11341     7.784327
13212     3.467915
...            ...
9546181  18.127914
8284616  18.127914
7934411  18.127914
1293261  18.127914
1700337  18.127914

[3196 rows x 1 columns]

Фунция формирования таблицы с предсказанием

In [9]:
def get_predictions(data, means):
    preds = data[['ID', 'date_']].set_index('ID')
    preds[targets] = means.loc[data.ID]
    preds.set_index('date_', append=True, inplace=True)
    preds.sort_index(inplace=True)
    return preds

In [10]:
train_preds = get_predictions(train, means)
train_preds

spd
ID      date_                
156     2016-01-01  81.977709
        2016-01-02  81.977709
        2016-01-03  81.977709
        2016-01-04  81.977709
        2016-01-05  81.977709
...                       ...
9998143 2016-10-27   5.746046
        2016-10-28   5.746046
        2016-10-29   5.746046
        2016-10-30   5.746046
        2016-10-31   5.746046

[918859 rows x 1 columns]

Метрика качества
$$\text{wrmse}\left(\text{spd}, \hat{\text{spd}}, \text{subs}\right)=\sqrt{\frac{\sum\limits_{i=1}^n\left(\left(\text{spd}_i-\hat{\text{spd}_i}\right)\cdot \text{subs}_i\right)^2}{\sum\limits_{i=1}^n\text{subs}_i^2}}$$

In [11]:
def wrmse(true, pred):
    return np.sqrt(np.sum(np.square((true.spd - pred.spd) * true.subs)) / np.sum(np.square(true.subs)))

In [12]:
wrmse(train.set_index(['ID', 'date_']).sort_index(), train_preds)

6.5694051154638435

In [13]:
test_preds = get_predictions(test, means)
test_preds

spd
ID      date_                
156     2016-11-02  81.977709
        2016-11-03  81.977709
        2016-11-04  81.977709
        2016-11-05  81.977709
        2016-11-06  81.977709
...                       ...
9998143 2017-02-25   5.746046
        2017-02-26   5.746046
        2017-02-27   5.746046
        2017-02-28   5.746046
        2017-03-01   5.746046

[380871 rows x 1 columns]

Сохранить данные 

In [14]:
test_preds.to_csv('submit.csv')